In [1]:
from __future__ import division
import os, sys, re, json, time, datetime, shutil
import itertools, collections
from importlib import reload
from IPython.display import display, HTML
import tensorflow as tf

from common import patched_numpy_io


from __future__ import print_function
from __future__ import division
import collections
import nltk
import numpy as np
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split
from nltk.tokenize.treebank import TreebankWordTokenizer

from sklearn.feature_extraction.text import TfidfTransformer

# Helper libraries
from common import utils, vocabulary

/home/younusahmed23/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
df = pd.read_csv('az_reduced_reviews.csv')

In [5]:
df.columns

Index(['business_id', 'stars', 'text'], dtype='object')

In [ ]:
biz_ids=df.groupby('business_id')
x=0
bizids={}
for name,group in biz_ids:
    #Processing restaurants that had more than three reviews. Number is up for debate.
    if len(group)>3:
        x+=1
        bizname="train_id_"+str(x)
        #This dictionary maps train_ids variables to business id. Just search bizids[train_id_1]=business_id
        bizids[bizname]=name
        count_vect = CountVectorizer(stop_words='english')
        X_train_counts = count_vect.fit_transform(group['text'])
        tfidf_transformer = TfidfTransformer()
        exec(bizname+'=tfidf_transformer.fit_transform(X_train_counts)')

In [ ]:
train_id_6

In [ ]:
df['text'][0]

# Importing Glove Vectors to use with Neural BOW

In [3]:
from GloveVectors import glove_helper; reload(glove_helper)

hands = glove_helper.Hands(ndim=300)  # 50, 100, 200, 300 dim are available"

Loading vectors from data/glove/glove.6B.zip
Parsing file: data/glove/glove.6B.zip:glove.6B.100d.txt
Found 400,000 words.
Parsing vectors... Done! (W.shape = (400003, 100))


In [4]:
#Split the data
x_df = df[df.stars != 3]
#ignore warning
x_df['binary_stars'] =  np.where(x_df['stars'] >= 4, 1, 0)
X_train, X_test, y_train, y_test = train_test_split(x_df.text, x_df.binary_stars, test_size=0.20, random_state=42)

/home/younusahmed23/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.


In [5]:
tokenizer = TreebankWordTokenizer()
x_tokens = tokenizer.tokenize('yo yo yo','what do i do')
x_tokens


['yo', 'yo', 'yo']

In [6]:
def canonicalize(x):
    return utils.canonicalize_words(x,wordset=hands.vocab.wordset)

In [7]:
def double(x):
   g=[]
   bad=[]
   for y in x:
       if len(y)>1 and "." not in y:
            bad.append(y)
            try:
                g.append(hands.vocab.word_to_id[y.strip('.')])
            except:
                print(y)
#    return [hands.vocab.word_to_id[y.strip('.')] for y in x if len(y)>1]
   return g

   

# Training a Neural Network

In [8]:
TF_SAVEDIR = "/tmp/w266/yelp_model"
checkpoint_filename = os.path.join(TF_SAVEDIR, "NeuralBOW")
trained_filename = os.path.join(TF_SAVEDIR, "Final_Neural_BOW_Trained")

In [9]:
from GloveVectors import models; reload(models)

x, y = X_train, y_train
batch_size = 64

# Specify model hyperparameters as used by model_fn
model_params = dict(V=hands.vocab.size, embed_dim=300, hidden_dims=[128,128], num_classes=2,
                    encoder_type='bow',
                    lr=0.01, optimizer='adam', beta=0.01,dropout_rate=0.25)
model_fn = models.classifier_model_fn

total_batches = 0
total_examples = 0
total_loss = 0
loss_ema = np.log(2)  # track exponential-moving-average of loss
ema_decay = np.exp(-1/10)  # decay parameter for moving average = np.exp(-1/history_length)

# Clear old log directory
shutil.rmtree(TF_SAVEDIR, ignore_errors=True)

if not os.path.isdir(TF_SAVEDIR):
    os.makedirs(TF_SAVEDIR)
    
with tf.Graph().as_default(), tf.Session() as sess:
    ##
    # Construct the graph here. No session.run calls - just wiring up Tensors.
    ##
    # Add placeholders so we can feed in data.
    x_ph_  = tf.placeholder(tf.float32, shape=[None,model_params['embed_dim']])  # [batch_size x embedding size]
    y_ph_  = tf.placeholder(tf.int32, shape=[None])              # [batch_size]
    
    # Construct the graph using model_fn
    features = {"ids": x_ph_,"hands":hands}  # note that values are Tensors
    estimator_spec = model_fn(features, labels=y_ph_, mode=tf.estimator.ModeKeys.TRAIN,
                              params=model_params)
    loss_     = estimator_spec.loss
    train_op_ = estimator_spec.train_op
    
    ##
    # Done constructing the graph, now we can make session.run calls.
    ##
    sess.run(tf.global_variables_initializer())
    saver = tf.train.Saver()
    
    # Run a single epoch
#     t0 = time.time()
    model = tf.estimator.Estimator(model_fn=models.classifier_model_fn, 
           params=model_params,
           )
    time=0
    for (bx, by) in utils.multi_batch_generator(batch_size, x, y):
        # feed NumPy arrays into the placeholder Tensors
        batchreview=pd.DataFrame(bx)['text']
        tokens=batchreview.map(tokenizer.tokenize).map(canonicalize)
        token_ids = pd.DataFrame(tokens.values)[0].map(double)
        inp=token_ids.map(lambda x: sum(hands.get_vector(y) for y in x))
        try:
#             feed_dict = {x_ph_: np.vstack(inp), y_ph_: by}
#             batch_loss, _ = sess.run([loss_, train_op_], feed_dict=feed_dict)

            train_input_fn = tf.estimator.inputs.numpy_input_fn(
                            x={"ids": np.vstack(inp)}, y=np.squeeze(pd.DataFrame(by).values),
                            batch_size=batch_size, num_epochs=1, shuffle=False)
            model.train(input_fn=train_input_fn)
            time+=1
            if time%100==0:
                model.evaluate(input_fn=train_input_fn)
        except:
            continue
#             saver.save(sess, checkpoint_filename, global_step=epoch)
        
  
    print("Completed one epoch in {:s}".format(utils.pretty_timedelta(since=t0)))
    saver.save(sess, trained_filename)

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/tmpbrxnyqyd', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7fbdd4909cc0>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 92.73

INFO:tensorflow:Loss for final step: 9.718879.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-16
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 17 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 13.676281, step = 17
INFO:tensorflow:Loss for final step: 13.676281.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-17
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 18 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 8.884596, step = 18
INFO:tensorflow:Loss for final step: 8.884596.

INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-33
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 34 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.6822009, step = 34
INFO:tensorflow:Loss for final step: 0.6822009.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-34
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 35 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.56664824, step = 35
INFO:tensorflow:Loss for final step: 0.56664824.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INF

INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-50
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 51 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.42228067, step = 51
INFO:tensorflow:Loss for final step: 0.42228067.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-51
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 52 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.415773, step = 52
INFO:tensorflow:Loss for final step: 0.415773.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:te

INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 68 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.55964524, step = 68
INFO:tensorflow:Loss for final step: 0.55964524.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-68
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 69 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.5695584, step = 69
INFO:tensorflow:Loss for final step: 0.5695584.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-69
INFO:tensorflow:Running local_init_op.
INF

...

INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-10072
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 10073 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.47365803, step = 10073
INFO:tensorflow:Loss for final step: 0.47365803.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-10073
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 10074 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.6337846, step = 10074
INFO:tensorflow:Loss for final step: 0.6337846.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create C

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-10089
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 10090 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.5445174, step = 10090
INFO:tensorflow:Loss for final step: 0.5445174.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-10090
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 10091 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.6376598, step = 10091
INFO:tensorflow:Loss for final step: 0.6376598.
INFO:tensorflow:Calling mo

INFO:tensorflow:loss = 0.61508906, step = 10105
INFO:tensorflow:Loss for final step: 0.61508906.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-10105
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 10106 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.47477168, step = 10106
INFO:tensorflow:Loss for final step: 0.47477168.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-10106
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 10107 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss =

INFO:tensorflow:Saving checkpoints for 10122 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.61773044, step = 10122
INFO:tensorflow:Loss for final step: 0.61773044.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-10122
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 10123 into /tmp/tmpbrxnyqyd/model.ckpt.
INFO:tensorflow:loss = 0.5445205, step = 10123
INFO:tensorflow:Loss for final step: 0.5445205.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-10123
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving c

NameError: name 't0' is not defined

In [9]:
!rm -rfv /tmp/tf_bow_sst_*

In [11]:
!tensorboard --logdir='/tmp/tf_bow_sst_20180609-2338' --port 6006

/home/younusahmed23/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
2018-07-19 22:31:45.781262: I tensorflow/core/platform/cpu_feature_guard.cc:140] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
TensorBoard 1.8.0 at http://w266:6006 (Press CTRL+C to quit)
W0719 22:31:52.944372 Thread-3 application.py:274] path /[[_dataImageSrc]] not found, sending 404
W0719 22:31:53.138972 Thread-2 application.py:274] path /[[_imageURL]] not found, sending 404
^C


In [ ]:
checkpoint_dir = "/tmp/tf_bow_sst_" + datetime.datetime.now().strftime("%Y%m%d-%H%M")
if os.path.isdir(checkpoint_dir):
    shutil.rmtree(checkpoint_dir)
# Write vocabulary to file, so TensorBoard can label embeddings.
# creates checkpoint_dir/projector_config.pbtxt and checkpoint_dir/metadata.tsv
print("To view training (once it starts), run:\n")
print("    tensorboard --logdir='{:s}' --port 6006".format(checkpoint_dir))
print("\nThen in your browser, open: http://localhost:6006")

To view training (once it starts), run:

    tensorboard --logdir='/tmp/tf_bow_sst_20180721-1330' --port 6006

Then in your browser, open: http://localhost:6006


#  Ignore Code below

In [ ]:
from GloveVectors import models; reload(models)

bx, by = X_train, y_train
batch_size = 50

# Specify model hyperparameters as used by model_fn
model_params = dict(V=hands.vocab.size, embed_dim=300, hidden_dims=[128], num_classes=2,
                    encoder_type='bow',
                    lr=0.1, optimizer='adagrad', beta=0.01,dropout_rate=0)

train_params = dict(batch_size=50, total_epochs=20, eval_every=2)



total_batches = 0
total_examples = 0
total_loss = 0
loss_ema = np.log(2)  # track exponential-moving-average of loss
ema_decay = np.exp(-1/10)  # decay parameter for moving average = np.exp(-1/history_length)

# Clear old log directory
shutil.rmtree(TF_SAVEDIR, ignore_errors=True)
saver = tf.train.Saver()
if not os.path.isdir(TF_SAVEDIR):
    os.makedirs(TF_SAVEDIR)
    
with tf.Graph().as_default(), tf.Session() as sess:
    ##
    # Construct the graph here. No session.run calls - just wiring up Tensors.


    ##
    # Done constructing the graph, now we can make session.run calls.
    ##
    sess.run(tf.global_variables_initializer())
    
    # Run a single epoch
    t0 = time.time()
    # feed NumPy arrays into the placeholder Tensors
    batchreview=pd.DataFrame(bx)['text']
    tokens=batchreview.map(tokenizer.tokenize).map(canonicalize)
    token_ids = pd.DataFrame(tokens.values)[0].map(double)
    inp=token_ids.map(lambda x: sum(hands.get_vector(y) for y in x))
    model = tf.estimator.Estimator(model_fn=models.classifier_model_fn, 
                           params=model_params,
                           )
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
                    x={"ids": np.vstack(inp)}, y=np.squeeze(pd.DataFrame(by).values),
                    batch_size=128, num_epochs=1, shuffle=False)
    model.train(input_fn=train_input_fn)
        # Compute some statistics
    

# Evaluate baseline Neural BOW Model

In [10]:
#### YOUR CODE HERE ####

testx, testy = X_test, y_test
batch_size = 50





# feed NumPy arrays into the placeholder Tensors
testreview=pd.DataFrame(testx)['text']
tokens=testreview.map(tokenizer.tokenize).map(canonicalize)
token_ids = pd.DataFrame(tokens.values)[0].map(double)
inp=token_ids.map(lambda x: sum(hands.get_vector(y) for y in x))


test_input_fn =  tf.estimator.inputs.numpy_input_fn(
                    x={"ids": np.vstack(inp.drop(labels=35335,axis=0))},\
    y=np.squeeze(pd.DataFrame(testy.drop(labels=35335,axis=0)).values),shuffle=False)



eval_metrics = model.evaluate(input_fn=test_input_fn, name="test")
#### END(YOUR CODE) ####
print("Accuracy on test set: {:.02%}".format(eval_metrics['accuracy']))
eval_metrics

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-07-21-21:42:35
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/tmpbrxnyqyd/model.ckpt-10129
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-07-21-21:42:37
INFO:tensorflow:Saving dict for global step 10129: accuracy = 0.7561777, cross_entropy_loss = 0.55547357, global_step = 10129, loss = 0.55547357
Accuracy on test set: 75.62%


{'accuracy': 0.7561777,
 'cross_entropy_loss': 0.55547357,
 'global_step': 10129,
 'loss': 0.55547357}

In [38]:
from GloveVectors import models; reload(models)

bx, by = X_test, y_test


# Specify model hyperparameters as used by model_fn
model_params = dict(V=hands.vocab.size, embed_dim=300, hidden_dims=[50,45,25], num_classes=2,
                    encoder_type='bow',
                    lr=0.1, optimizer='adagrad', beta=0.01)


with tf.Graph().as_default(), tf.Session() as sess:
    ##
    # Construct the graph here. No session.run calls - just wiring up Tensors.
    ##
    # Add placeholders so we can feed in data.
    x_ph_  = tf.placeholder(tf.float32, shape=[None,model_params['embed_dim']])  # [batch_size x embedding size]
    y_ph_  = tf.placeholder(tf.int32, shape=[None])              # [batch_size]
    
    # Construct the graph using model_fn
    

    loss_     = estimator_spec.loss
    train_op_ = estimator_spec.train_op
#     eval_metrics=estimator_spec.eval_metrics
    ##

    
    # Run a single epoch
    t0 = time.time()
    # feed NumPy arrays into the placeholder Tensors
    batchreview=pd.DataFrame(bx)['text']
    tokens=batchreview.map(tokenizer.tokenize).map(canonicalize)
    token_ids = pd.DataFrame(tokens.values)[0].map(double)
    inp=token_ids.map(lambda x: sum(hands.get_vector(y) for y in x))
    feed_dict = {x_ph_: np.vstack(inp), y_ph_: by}

    features = {"ids": tf.constant(np.vstack(inp)),"hands":hands}  # note that values are Tensors
    estimator_spec = model_fn(features, labels=tf.constant(pd.DataFrame(by[0:10])['binary_stars']),\
                              mode=tf.estimator.ModeKeys.EVAL,params=model_params)


        # Compute some statistics
       

In [43]:
bad=[]
elem=0
for y in inp:
    try:
        print(y.shape[0])
    except:
        print(y)
        bad.append((y,elem))
    elem+=1
        

300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300


300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300


300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300


300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300


300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300


...

300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300


300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300


300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300


300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300


300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
300
